# Documentación del Notebook: Predicción de Coeficientes de Zernike a partir de Imágenes Hartmann-Shack para una arquitectura Vision Transformer.

Este notebook implementa un pipeline completo para entrenar y evaluar un modelo de `Deep Learning` (basado en ResNet-18) capaz de predecir 20 coeficientes de Zernike a partir de imágenes simuladas de un sensor Hartmann-Shack. El proceso incluye la instalación de dependencias, descarga y preparación del dataset, definición del modelo, entrenamiento, evaluación y visualización de resultados.

## Descripción del Proceso de Generación de Imágenes

Este documento describe el proceso utilizado para generar el dataset de imágenes, centrándose en la simulación de aberraciones ópticas mediante Coeficientes de Zernike y su representación a través del método de Hartmann-Shack.

### 1. Coeficientes de Zernike

Los Coeficientes de Zernike son una serie de polinomios ortogonales utilizados comúnmente en óptica para describir las aberraciones de un frente de onda. En este dataset, cada imagen es generada a partir de un conjunto de **20 coeficientes de Zernike**.

*   **Número de Coeficientes:** Se utilizan los primeros 20 coeficientes de Zernike (excluyendo el pistón, que solo representa un cambio de fase global y no afecta la forma de la imagen).
*   **Rango de Valores:** Cada uno de estos 20 coeficientes de Zernike varía dentro de un rango de **-8 a 8 micrometros**.
    *   Este rango permite simular una amplia variedad de aberraciones, desde las más comunes (como el desenfoque y el astigmatismo) hasta las de orden superior, capturando la complejidad de los frentes de onda que se encuentran en sistemas ópticos reales o en el ojo humano.
    *   La variabilidad de los coeficientes asegura una diversidad en el dataset, crucial para entrenar modelos robustos de aprendizaje automático.

### 2. Método de Simulación Hartmann-Shack

La generación de las imágenes se realiza mediante la simulación de un **sensor de frente de onda Hartmann-Shack**. Este método es fundamental para la caracterización de las aberraciones:

*   **Principio:** Un sensor Hartmann-Shack consiste en una matriz de microlentes que dividen el frente de onda incidente en múltiples pequeños sub-aperturas. Cada microlente enfoca la luz en un punto en un detector (por ejemplo, un CCD).
*   **Detección de Aberraciones:** Si el frente de onda es plano y perfecto, todos los puntos focales de las microlentes formarán una cuadrícula regular. Sin embargo, en presencia de aberraciones, los puntos focales se desplazan de sus posiciones ideales. La magnitud y dirección de estos desplazamientos son directamente proporcionales a la pendiente local del frente de onda.
*   **Generación de Imágenes:** En esta simulación, los 20 coeficientes de Zernike definen un frente de onda aberrado. Este frente de onda es entonces "medido" virtualmente por un sensor Hartmann-Shack simulado. La salida de esta simulación es una imagen que representa los desplazamientos de los spots focales, que es la imagen que compone el dataset.

### Resumen del Proceso

1.  Se seleccionan aleatoriamente 20 coeficientes de Zernike, cada uno dentro del rango [-1, 1].

2. Los coeficientes 1 y 2 varian entre -17 y 17 micrómetros generados aleatoriamente, el coeficiente 0 no se toma puesto que no aporta información relevante.
3.  Estos coeficientes definen un frente de onda con aberraciones específicas.
4.  Se simula cómo un sensor Hartmann-Shack "vería" 4ste frente de onda aberrado.
5.  La salida de esta simulación (la imagen de los spots desplazados) se guarda como una entrada en el dataset.

Este enfoque permite crear un dataset diverso y representativo de frentes de onda con aberraciones conocidas y también se crea una cantida de imágines específica para garantizar un rango dinámico amplo para ser evaluado, lo que es ideal para entrenar y evaluar modelos capaces de predecir o clasificar aberraciones ópticas a partir de imágenes de Hartmann-Shack.

### Instalación de Librerías

Este bloque de código se encarga de instalar todas las librerías necesarias para el proyecto. Utiliza `pip install --quiet` para una instalación silenciosa de paquetes como `numpy`, `pandas`, `pillow`, `matplotlib`, `tqdm`, `scipy` (para correlación de Pearson), `scikit-learn` (para MAE, R2), `plotly` (para gráficas interactivas) y las dependencias de `PyTorch` (`torch`, `torchvision`, `torchaudio`) compatibles con CUDA. También instala `gdown` para la descarga desde Google Drive. Al finalizar, imprime un mensaje de confirmación.

## 1. Configuración del Entorno

Esta sección se encarga de preparar el entorno de ejecución, instalando todas las librerías necesarias para el desarrollo y la ejecución del modelo.

In [1]:
# ============================================================
# 🔧 Instalación de todas las librerías necesarias (Colab)
# ============================================================

# Básicos
!pip install --quiet numpy pandas pillow matplotlib tqdm numpy

# SciPy (para correlación Pearson)
!pip install --quiet scipy

# Scikit-Learn (MAE, R2)
!pip install --quiet scikit-learn

# Plotly (gráficas interactivas)
!pip install --quiet plotly

# PyTorch + TorchVision compatible con CUDA (Colab)
# Colab ya incluye PyTorch, pero forzamos actualización estable.
!pip install --quiet torch torchvision torchaudio --index-url https://download.pytorch.org/whl/cu118

!pip install gdown
print("Todas las dependencias han sido instaladas correctamente.")

Todas las dependencias han sido instaladas correctamente.


## 2. Importación de Librerías

Este bloque importa todas las librerías y módulos que se utilizarán a lo largo del notebook. Incluye módulos para:
- **Manejo de archivos y rutas**: `os`, `zipfile`, `gdown`, `re`.
- **Manipulación de datos numéricos y estructuras**: `numpy` (como `np`), `PIL` (como `Image`), `pandas` (como `pd`), `random`.
- **Estadísticas y métricas**: `scipy.stats` (para correlación de Pearson), `sklearn.metrics` (para MAE, R2).
- **PyTorch**: `torch`, `torch.nn`, `torch.nn.functional` (como `F`), `torch.optim`, `torch.utils.data` (`Dataset`, `DataLoader`).
- **Procesamiento de imágenes**: `torchvision.transforms` (como `transforms`), `torchvision.transforms.ToPILImage`, `torchvision.models.feature_extraction.create_feature_extractor`.
- **Visualización**: `tqdm` (para barras de progreso), `matplotlib.pyplot` (como `plt`), `plotly.express` (como `px`), `plotly.graph_objects` (como `go`), `plotly.subplots.make_subplots`.

In [2]:
import os
import zipfile
import gdown
import re

import numpy as np
from PIL import Image
import pandas as pd
import random


import scipy.stats as stats  # Para calcular la correlación de Pearson
from sklearn.metrics import mean_absolute_error, r2_score

import torch
import torch.nn as nn
import torch.nn.functional as F

import torch.optim as optim
from torch.utils.data import Dataset, DataLoader

import torchvision.transforms as transforms
from torchvision.transforms import ToPILImage
from torchvision.models.feature_extraction import create_feature_extractor
from torchvision.models import resnet18, ResNet18_Weights

from tqdm import tqdm  # Para mostrar el progreso

import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

## 3. Descarga y Preparación del Dataset

Esta sección maneja la adquisición y descompresión de los datos, así como la verificación de la estructura de archivos. El dataset contiene imágenes de Hartmann-Shack y sus correspondientes coeficientes de Zernike.

### 3.1 Descarga de Datos desde Google Drive

Este bloque define un `folder_id` de Google Drive y construye una URL para la descarga. Luego, utiliza la librería `gdown` para descargar la carpeta completa especificada por la URL. La descarga se guarda en el directorio `./data` dentro del entorno de Colab. Al finalizar, muestra un mensaje de confirmación de la descarga.

In [3]:
folder_id = "14--HWvqgHGtH5TVJu3sqSGAp2tEYTsYi"
url = f"https://drive.google.com/drive/folders/{folder_id}"

print("Descargando carpeta desde Google Drive...")
gdown.download_folder(url, output="./data", remaining_ok=True)

print("✔️ Descarga completa. Los archivos están en ./data")

Descargando carpeta desde Google Drive...


Retrieving folder contents


Processing file 1a65zvPWX61PEHfdEwhU9OU3Aqq_NLLf1 archive.zip


Retrieving folder contents completed
Building directory structure
Building directory structure completed
Downloading...
From (original): https://drive.google.com/uc?id=1a65zvPWX61PEHfdEwhU9OU3Aqq_NLLf1
From (redirected): https://drive.google.com/uc?id=1a65zvPWX61PEHfdEwhU9OU3Aqq_NLLf1&confirm=t&uuid=e14ea214-cd5d-475e-b410-2e33240eb0a1
To: /content/data/archive.zip
100%|██████████| 743M/743M [00:08<00:00, 84.8MB/s]

✔️ Descarga completa. Los archivos están en ./data



Download completed


### 3.2 Descompresión del Dataset

Este bloque de código se encarga de descomprimir el archivo `archive.zip` descargado en la etapa anterior. Primero, verifica si el archivo `archive.zip` existe en la ruta especificada (`./data/archive.zip`). Si no lo encuentra, lanza un error. Luego, utiliza la librería `zipfile` para extraer todo el contenido del archivo zip en el directorio `./data`. Al finalizar, imprime un mensaje de confirmación de que la descompresión fue exitosa.

In [4]:
zip_path = "./data/archive.zip"
extract_to = "./data"

# Verificar si existe
if not os.path.exists(zip_path):
    raise FileNotFoundError(f"No se encontró el archivo: {zip_path}")

print("Descomprimiendo dataset (esto puede tardar)...")

with zipfile.ZipFile(zip_path, 'r') as zip_ref:
    zip_ref.extractall(extract_to)

print("Listo ✔️")


Descomprimiendo dataset (esto puede tardar)...
Listo ✔️


### 3.3 Verificación de la Estructura de Directorios

Este bloque de código simple recorre el directorio `./content/data` y sus subdirectorios utilizando `os.walk`. Su propósito es imprimir la estructura de directorios, lo cual es útil para verificar que los archivos se hayan descargado y descomprimido correctamente y para entender la organización de los datos.

In [5]:
for root, _, _ in os.walk("./data", topdown=True):
    print(root)

./data
./data/DataSet_Zernike_20_Coef
./data/DataSet_Zernike_20_Coef/Train
./data/DataSet_Zernike_20_Coef/Validation
./data/DataSet_Zernike_20_Coef/Test


## 4. Configuración del Dataset y DataLoader

Esta sección define cómo se cargarán y preprocesarán las imágenes y sus coeficientes asociados para el entrenamiento y la validación del modelo. Se verifica la disponibilidad de GPU y se define una clase personalizada para el dataset.

### 4.1 Clase `CombinedDataset`

La clase `CombinedDataset` hereda de `torch.utils.data.Dataset` y se encarga de:
- Cargar imágenes PNG y sus respectivos archivos de texto de coeficientes.
- Aplicar transformaciones a las imágenes (redimensionamiento, conversión a tensor).
- Asegurar que cada imagen tenga un archivo de coeficientes asociado.
- Mezclar aleatoriamente los datos.

La función `is_valid_number` es una utilidad para verificar la validez de los números en los archivos de coeficientes.

In [6]:
# Verificar si GPU está disponible y configurar dispositivo
# Configuración general
torch.backends.cudnn.benchmark = True
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# Clase para cargar imágenes desde múltiples directorios
class CombinedDataset(Dataset):
    def __init__(self, directories, transform=None):
        self.transform = transform
        self.samples = []

        # Recorrer cada directorio y almacenar archivos en una lista
        for image_dir in directories:
            filenames = [f for f in os.listdir(image_dir) if f.endswith('.png')]
            for filename in filenames:
                img_path = os.path.join(image_dir, filename)
                coef_path = os.path.join(image_dir, f'coef_{filename[4:-4]}.txt')
                if os.path.exists(coef_path):  # Asegurar que existe el archivo de coeficientes
                    self.samples.append((img_path, coef_path))

        # Mezclar aleatoriamente los datos combinados
        random.shuffle(self.samples)

    def __len__(self):
        return len(self.samples)

    def __getitem__(self, idx):
        img_path, coef_path = self.samples[idx]

        # Cargar imagen
        image = Image.open(img_path).convert('L')

        if self.transform:
            image = self.transform(image)

        # Leer coeficientes línea por línea
        with open(coef_path, 'r') as f:
            lines = f.readlines()
            coefficients = [float(x.strip()) for x in lines if is_valid_number(x.strip())]

        if len(coefficients) == 0:
            raise ValueError(f"Archivo sin coeficientes válidos: {coef_path}")

        coefficients = torch.tensor(coefficients, dtype=torch.float32)

        return image, coefficients

def is_valid_number(s):
    """ Verifica si 's' es un número válido, incluyendo notación científica. """
    try:
        float(s)  # Intenta convertir a float
        return True
    except ValueError:
        return False

# Transformación para las imágenes
transform = transforms.Compose([
    transforms.Grayscale(num_output_channels = 1),
    transforms.Resize((256, 256)), # 256, 256
    transforms.ToTensor()
])


batch_size = 32

# Rutas de los datos de entrenamiento y validación
train_pure = './data/DataSet_Zernike_20_Coef/Train'
#train_random = '/kaggle/input/dataset-ojoartificial/Dataset_exp_OjoArtificial_R/Dataset_exp_OjoArtificial_R/Train'


validation_puros = './data/DataSet_Zernike_20_Coef/Validation'
#validation_random = '/kaggle/input/dataset-ojoartificial/Dataset_exp_OjoArtificial_R/Dataset_exp_OjoArtificial_R/Validation'

train_dirs = [train_pure]
validation_dirs = [validation_puros]

# Crear DataLoaders
train_dataset = CombinedDataset(train_dirs, transform=transform)
validation_dataset = CombinedDataset(validation_dirs, transform=transform)

# DataLoader optimizado
train_loader = DataLoader(
    train_dataset,
    batch_size=32,       # o el máximo que soporte tu memoria GPU
    shuffle=True,
    num_workers=4,
    pin_memory=True
)

validation_loader = DataLoader(
    validation_dataset,
    batch_size=32,
    shuffle=False,
    num_workers=4,
    pin_memory=True
)

/usr/local/lib/python3.12/dist-packages/torch/utils/data/dataloader.py:627: UserWarning: This DataLoader will create 4 worker processes in total. Our suggested max number of worker in current system is 2, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  warnings.warn(


## 5. Definición del Modelo

Esta sección define la arquitectura del modelo Vision Transformer utilizado para la predicción de los coeficientes de Zernike. El modelo se compone de varias partes clave:

### 5.1 `PatchEmbedding`

Esta clase es responsable de dividir la imagen de entrada en parches y proyectarlos en un espacio de incrustación (embedding). Utiliza una capa convolucional (`nn.Conv2d`) con un tamaño de kernel y stride igual al `patch_size` para transformar los parches de imagen en vectores.

### 5.2 `TransformerEncoderLayer`

Esta clase implementa un bloque estándar del encoder de un Transformer. Incluye:
- **Normalización de Capa (`nn.LayerNorm`)**: Aplicada antes de la atención y la MLP.
- **Mecanismo de Autoatención Multi-cabeza (`nn.MultiheadAttention`)**: Permite al modelo ponderar la importancia de diferentes parches de la imagen entre sí.
- **Red Neuronal Multicapa (MLP)**: Una red *feed-forward* que procesa las representaciones de los parches después de la atención.
- **Conexiones Residuales**: Se aplican después de la atención y la MLP para facilitar el flujo de gradientes.

### 5.3 `VisionTransformer`

Esta es la clase principal del modelo Vision Transformer, que orquesta los componentes anteriores:
- **`patch_embed`**: Instancia de `PatchEmbedding` para procesar la imagen de entrada.
- **`cls_token`**: Un token aprendible que se concatena con los parches de la imagen y cuya salida final se utiliza para la predicción. Representa la información global de la imagen.
- **`pos_embed`**: Incrustaciones posicionales aprendibles que se añaden a los tokens de parche para inyectar información sobre la ubicación espacial de los parches.
- **`blocks`**: Una secuencia de `TransformerEncoderLayer` que procesan las representaciones de los parches.
- **Capa Final (`fc`)**: Una capa lineal que mapea la representación del `cls_token` a los 20 coeficientes de Zernike.

### Creación e Inicialización del Modelo

El modelo `VisionTransformer` se inicializa con los parámetros definidos (tamaño de imagen, tamaño de parche, dimensión de embedding, profundidad, número de cabezas y número de clases de salida) y se mueve al dispositivo (`cuda` o `cpu`) disponible. Se define la función de pérdida (`nn.MSELoss`) y el optimizador (`optim.Adam`) para el entrenamiento.

In [8]:
class PatchEmbedding(nn.Module):
    def __init__(self, img_size=224, patch_size=16, in_channels=1, embed_dim=128):
        super().__init__()

        self.patch_size = patch_size

        self.proj = nn.Conv2d(
            in_channels,
            embed_dim,
            kernel_size=patch_size,
            stride=patch_size
        )

    def forward(self, x):
        # x → [B, C, H, W]
        x = self.proj(x)  # → [B, embed_dim, H/patch, W/patch]
        x = x.flatten(2)  # → [B, embed_dim, N_patches]
        x = x.transpose(1, 2)  # → [B, N_patches, embed_dim]
        return x


In [9]:
class TransformerEncoderLayer(nn.Module):
    def __init__(self, embed_dim=128, num_heads=4, mlp_ratio=4.0):
        super().__init__()

        self.norm1 = nn.LayerNorm(embed_dim)
        self.attn = nn.MultiheadAttention(embed_dim, num_heads, batch_first=True)

        self.norm2 = nn.LayerNorm(embed_dim)
        hidden_dim = int(embed_dim * mlp_ratio)

        self.mlp = nn.Sequential(
            nn.Linear(embed_dim, hidden_dim),
            nn.GELU(),
            nn.Linear(hidden_dim, embed_dim),
        )

    def forward(self, x):
        # Self Attention + residual
        attn_out, _ = self.attn(self.norm1(x), self.norm1(x), self.norm1(x))
        x = x + attn_out

        # MLP + residual
        x = x + self.mlp(self.norm2(x))

        return x


In [7]:
class VisionTransformer(nn.Module):
    def __init__(self, img_size=224, patch_size=16, embed_dim=128, depth=6, num_heads=4, num_classes=10):
        super().__init__()

        self.patch_embed = PatchEmbedding(img_size, patch_size,1, embed_dim)

        num_patches = (img_size // patch_size) ** 2

        # class token
        self.cls_token = nn.Parameter(torch.zeros(1, 1, embed_dim))

        # positional embeddings
        self.pos_embed = nn.Parameter(torch.zeros(1, num_patches + 1, embed_dim))

        # transformer blocks
        self.blocks = nn.Sequential(
            *[TransformerEncoderLayer(embed_dim, num_heads) for _ in range(depth)]
        )

        # capa final (similar a tu implementación CNN)
        self.norm = nn.LayerNorm(embed_dim)
        self.fc = nn.Linear(embed_dim, num_classes)

        nn.init.trunc_normal_(self.pos_embed, std=0.02)
        nn.init.trunc_normal_(self.cls_token, std=0.02)

    def forward(self, x):
        B = x.size(0)

        x = self.patch_embed(x)

        cls_token = self.cls_token.expand(B, -1, -1)
        x = torch.cat((cls_token, x), dim=1)

        x = x + self.pos_embed
        x = self.blocks(x)

        x = self.norm(x[:, 0])   # solo el token cls
        out = self.fc(x)

        return out


In [13]:
# Crear el modelo
model = VisionTransformer(
    img_size=256,
    patch_size=16,
    embed_dim=128,
    depth=6,
    num_heads=4,
    num_classes=20
).to(device)

# Mover el modelo a GPU si está disponible
model = model.to(device)

criterion = nn.MSELoss()
optimizer = optim.Adam(model.parameters(), lr=0.001)

### 6. Entrenamiento y Evaluación del Modelo

Esta sección describe el proceso de entrenamiento del modelo y su evaluación en el conjunto de validación.

#### 6.1 `evaluate_model` (Función de Evaluación)

Esta función se encarga de calcular la pérdida de validación y la correlación de Pearson entre las predicciones del modelo y los valores reales. Se ejecuta en modo `torch.no_grad()` para deshabilitar el cálculo de gradientes y acelerar la evaluación.
- **Cálculo de Pérdida**: Calcula la pérdida MSE promedio en el conjunto de datos.
- **Correlación de Pearson**: Calcula el coeficiente de correlación de Pearson para cada uno de los 20 coeficientes de Zernike individualmente, proporcionando una métrica de la linealidad de la relación entre las predicciones y los valores reales.

In [11]:
# Función para evaluación con cálculo de correlación
def evaluate_model(loader, model):
    total_loss = 0.0
    criterion = nn.MSELoss()
    all_predictions = []
    all_labels = []

    with torch.no_grad():
        for images, labels in loader:
            images, labels = images.to(device), labels.to(device)
            outputs = model(images)
            loss = criterion(outputs, labels)
            total_loss += loss.item()
            all_predictions.append(outputs.cpu().numpy())
            all_labels.append(labels.cpu().numpy())


    # Convertir listas en arrays de NumPy
    all_predictions = np.concatenate(all_predictions, axis=0)
    all_labels = np.concatenate(all_labels, axis=0)

    # Calcular coeficiente de correlación por cada coeficiente de salida (18 valores)
    correlations = []
    for i in range(20):  # Asumiendo 18 coeficientes de salida
        corr, _ = stats.pearsonr(all_predictions[:, i], all_labels[:, i])
        correlations.append(corr)

    return total_loss / len(loader), correlations


#### 6.2 Bucle de Entrenamiento

El bucle de entrenamiento itera durante un número definido de `epochs` (épocas):
- **Modo `model.train()`**: Establece el modelo en modo de entrenamiento.
- **Bucle de Lotes (`tqdm`)**: Procesa los datos por lotes utilizando `train_loader`, mostrando una barra de progreso interactiva.
- **Optimización**: Para cada lote:
    - Mueve imágenes y etiquetas a la GPU.
    - Pone a cero los gradientes del optimizador.
    - Realiza una pasada hacia adelante (`model(images)`).
    - Calcula la pérdida (`criterion(outputs, labels)`).
    - Realiza una pasada hacia atrás (`loss.backward()`) para calcular los gradientes.
    - Actualiza los pesos del modelo (`optimizer.step()`).
- **Evaluación en Validación**: Al final de cada época, se llama a `evaluate_model` para obtener la pérdida y las correlaciones en el conjunto de validación.
- **Guardado del Modelo**: Se guarda el estado del modelo (`best_resnet18_model_2_replicate.pth`) si la pérdida de validación actual es la mejor hasta el momento.

In [14]:
# Entrenamiento con validación en cada época
epochs = 1
best_val_loss = float('inf')

train_losses = []
val_losses = []

for epoch in range(epochs):
    model.train()
    running_loss = 0.0
    with tqdm(train_loader, unit="batch") as tepoch:
        for images, labels in tepoch:
            tepoch.set_description(f"Epoch {epoch+1}")
            images, labels = images.to(device), labels.to(device)  # Mover datos a la GPU
            optimizer.zero_grad()
            outputs = model(images)
            loss = criterion(outputs, labels)
            loss.backward()
            optimizer.step()
            running_loss += loss.item()
            tepoch.set_postfix(loss=loss.item())

    # Calcular pérdidas promedio en entrenamiento y validación
    train_loss = running_loss / len(train_loader)
    val_loss, correlations = evaluate_model(validation_loader, model)


    train_losses.append(train_loss)
    val_losses.append(val_loss)

    print(f"Época [{epoch+1}/{epochs}], Pérdida de entrenamiento: {train_loss:.4f}, Pérdida de validación: {val_loss:.4f}")

    # Guardar el mejor modelo basado en validación
    if val_loss < best_val_loss:
        best_val_loss = val_loss
        torch.save(model.state_dict(), "best_resnet18_model_2_replicate.pth")
        print("Modelo guardado con menor pérdida de validación.")

  0%|          | 0/850 [00:00<?, ?batch/s]/usr/local/lib/python3.12/dist-packages/torch/utils/data/dataloader.py:627: UserWarning: This DataLoader will create 4 worker processes in total. Our suggested max number of worker in current system is 2, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  warnings.warn(
Epoch 1: 100%|██████████| 850/850 [03:25<00:00,  4.14batch/s, loss=0.76]


Época [1/1], Pérdida de entrenamiento: 1.5457, Pérdida de validación: 0.9983
Modelo guardado con menor pérdida de validación.


### 7. Visualización de Resultados de Entrenamiento y Correlación

Esta sección contiene funciones para visualizar de forma interactiva la evolución de la pérdida durante el entrenamiento y las correlaciones de Pearson de los coeficientes.

#### 7.1 `plot_loss_interactive`

Esta función utiliza `plotly.graph_objects` para generar un gráfico interactivo que muestra la pérdida de entrenamiento y la pérdida de validación a lo largo de las épocas. Esto permite observar si el modelo está sobreajustando o subajustando, y cómo converge la pérdida. El gráfico se guarda también como un archivo HTML (`Evolutions_loss.html`).

#### 7.2 `plot_correlation_interactive`

Esta función genera un diagrama de barras interactivo utilizando `plotly.express` para visualizar el coeficiente de correlación de Pearson para cada uno de los 20 coeficientes de Zernike. Un valor cercano a 1 indica una fuerte correlación positiva, mientras que un valor cercano a -1 indica una fuerte correlación negativa. Esto ayuda a identificar qué coeficientes son predichos con mayor o menor precisión. El gráfico se guarda también como un archivo HTML (`Correlations.html`).

In [15]:
# Graficar la pérdida en entrenamiento y validación de forma interactiva
def plot_loss_interactive(epochs, train_losses, val_losses):
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=list(range(epochs)), y=train_losses, mode='lines', name='Entrenamiento'))
    fig.add_trace(go.Scatter(x=list(range(epochs)), y=val_losses, mode='lines', name='Validación', line=dict(dash='dash')))

    fig.update_layout(title='Evolución de la Pérdida durante el Entrenamiento',
                      xaxis_title='Época',
                      yaxis_title='Pérdida',
                      legend_title='Dataset')

    fig.show()
    fig.write_html("Evolutions_loss.html")

# Graficar la correlación de los coeficientes de forma interactiva
def plot_correlation_interactive(correlations):
    indices = list(range(1, len(correlations) + 1))
    fig = px.bar(x=indices, y=correlations, labels={'x': 'Índice del Coeficiente', 'y': 'Coeficiente de Correlación'},
                 title='Correlación entre Predicciones y Valores Reales')
    fig.update_yaxes(range=[-1, 1])
    fig.show()
    fig.write_html("Correlations.html")



In [16]:
# Imprimir resultados
print(f"\nValidation Loss (MSE): {val_loss:.4f}")
print("\nCoeficientes de correlación por coeficiente de salida:")
for i, corr in enumerate(correlations):
    print(f"Coeficiente {i+1}: {corr:.4f}")
print("")


Validation Loss (MSE): 0.9983

Coeficientes de correlación por coeficiente de salida:
Coeficiente 1: 0.8623
Coeficiente 2: 0.8763
Coeficiente 3: -0.0191
Coeficiente 4: 0.0498
Coeficiente 5: 0.0227
Coeficiente 6: 0.0366
Coeficiente 7: 0.1538
Coeficiente 8: 0.0590
Coeficiente 9: 0.0095
Coeficiente 10: -0.0065
Coeficiente 11: 0.0199
Coeficiente 12: 0.1309
Coeficiente 13: 0.1709
Coeficiente 14: 0.0002
Coeficiente 15: 0.0545
Coeficiente 16: 0.0875
Coeficiente 17: 0.1190
Coeficiente 18: 0.0459
Coeficiente 19: 0.0023
Coeficiente 20: -0.0166



In [ ]:
# Grafica interactiva
plot_correlation_interactive(correlations)
plot_loss_interactive(epochs, train_losses, val_losses)

### 8. Evaluación Completa en Conjuntos de Prueba y Validación (Métricas Detalladas)

Esta sección define una función robusta para evaluar el modelo en un conjunto de datos (típicamente el de prueba) y generar diversas métricas y visualizaciones de los errores de predicción.

#### 8.1 `evaluate_and_plot_test`

Esta función realiza una evaluación exhaustiva del modelo y genera gráficos interactivos:
- **Pérdida MSE y RMSE**: Calcula el Error Cuadrático Medio (MSE) y la Raíz del Error Cuadrático Medio (RMSE).
- **MAE**: Calcula el Error Absoluto Medio (MAE).
- **R²**: Calcula el coeficiente de determinación R².
- **Diagrama de Cajas de Errores**: Utiliza `plotly.express` para mostrar la distribución de los errores de predicción para cada coeficiente de Zernike. Esto es útil para identificar la variabilidad y la tendencia central de los errores por coeficiente.
- **Histograma de Errores de Predicción**: Genera un histograma general de todos los errores de predicción, dando una idea de la distribución global de los errores.
- **Frecuencia del Error por Coeficiente (Líneas)**: Crea un gráfico de líneas superpuestas mostrando la distribución de frecuencia de los errores para cada coeficiente, lo que permite una comparación visual de la dispersión de los errores entre coeficientes.

Todos los gráficos interactivos se guardan también como archivos HTML (`Boxplot.html`, `Histogram_Prediction_Errors.html`, `Lineplot_Errors_Per_Coefficient.html`).

In [17]:
# Función para evaluar el modelo y graficar resultados de forma interactiva
def evaluate_and_plot_test(loader, model, criterion, dataset_name=""):
    model.eval()
    total_loss = 0.0
    all_labels = []
    all_predictions = []

    with torch.no_grad():
        for images, labels in loader:
            images, labels = images.to(device), labels.to(device)
            outputs = model(images)
            loss = criterion(outputs, labels)
            total_loss += loss.item()

            all_labels.append(labels.cpu().numpy())
            all_predictions.append(outputs.cpu().numpy())

    mse_avg_loss = total_loss / len(loader)
    rmse_avg = torch.sqrt(torch.tensor(mse_avg_loss))

    # Convertir listas en arrays para análisis
    all_labels = np.concatenate(all_labels, axis=0)
    all_predictions = np.concatenate(all_predictions, axis=0)

    # Calcular métricas adicionales
    mae = mean_absolute_error(all_labels, all_predictions)
    r2 = r2_score(all_labels, all_predictions)

    # Imprimir métricas
    print(f'[{dataset_name}] Loss (MSE): {mse_avg_loss:.4f}')
    print(f'[{dataset_name}] Loss (RMSE): {rmse_avg:.4f}')
    print(f'[{dataset_name}] MAE: {mae:.4f}')
    print(f'[{dataset_name}] R²: {r2:.4f}')

    # Calcular el error absoluto para cada coeficiente
    errors = all_predictions - all_labels

    df_errors = pd.DataFrame(errors, columns=[f'Coef {i+1}' for i in range(errors.shape[1])])
    df_melted = df_errors.melt(var_name='Coeficiente', value_name='Error')

    fig = px.box(df_melted, x='Coeficiente', y='Error', color='Coeficiente',
                 title='Diagrama de Cajas de Errores por Coeficiente')

    # Crear histograma interactivo de errores

    fig2 = px.histogram(errors, nbins=30, labels={'value': 'Prediction Error'},
                        title=f'{dataset_name}: Histogram of Prediction Errors', opacity=0.7)

    # Crear figura de líneas para errores por coeficiente
    fig3 = go.Figure()

    num_bins = 100  # Puedes ajustar este número según el detalle deseado

    # Crear una línea para cada coeficiente
    for i in range(errors.shape[1]):
        hist, bin_edges = np.histogram(errors[:, i], bins=num_bins)
        bin_centers = 0.5 * (bin_edges[:-1] + bin_edges[1:])

        fig3.add_trace(go.Scatter(
            x=bin_centers,
            y=hist,
            mode='lines',
            name=f'Coef {i+1}'
        ))

    fig3.update_layout(
        title=f'{dataset_name}: Frecuencia del Error de Predicción por Coeficiente',
        xaxis_title='Error de Predicción',
        yaxis_title='Frecuencia',
        template='plotly_white'
    )


    fig.show()
    fig2.show()
    fig3.show()

    fig.write_html("Boxplot.html")
    fig2.write_html("Histogram_Prediction_Errors.html")
    fig3.write_html("Lineplot_Errors_Per_Coefficient.html")

    return rmse_avg, mse_avg_loss, mae, r2, all_predictions, all_labels, errors

#### 8.2 Creación de DataLoader para el Conjunto de Prueba

Se configura un `DataLoader` específico para el conjunto de prueba, `test_loader`, para cargar los datos de manera eficiente y sin `shuffle` (mezcla) ya que no es necesario para la evaluación.

In [18]:
# Crear DataLoader para Test y Validation
test_pure = './data/DataSet_Zernike_20_Coef/Test'
#test_random = '/kaggle/input/dataset-ojoartificial/Dataset_exp_OjoArtificial_R/Dataset_exp_OjoArtificial_R/Test'

test_dirs = [test_pure]


test_dataset = CombinedDataset(test_dirs, transform=transform)
test_loader = DataLoader(test_dataset, batch_size=32, shuffle=False)


# Definir criterio de pérdida
criterion = torch.nn.MSELoss()

#### 8.3 Evaluación del Modelo en el Conjunto de Prueba

Se llama a la función `evaluate_and_plot_test` para obtener y visualizar las métricas de rendimiento del modelo en el conjunto de prueba (`Test Set`). Se almacenan las predicciones, las etiquetas reales y los errores para análisis posteriores.

In [19]:
# Evaluar en los conjuntos de Test y Validation
test_loss,test_loss_rmse, test_mae, test_r2, all_predictions, all_labels, errors = evaluate_and_plot_test(test_loader, model, criterion, "Test Set")

[Test Set] Loss (MSE): 1.0216
[Test Set] Loss (RMSE): 1.0107
[Test Set] MAE: 0.6408
[Test Set] R²: 0.0582


### 9. Guardado de Resultados en Archivos CSV

Esta sección se encarga de persistir los resultados clave del modelo en archivos CSV para su análisis posterior fuera del notebook o para replicabilidad.

#### 9.1 Preparación y Guardado de Predicciones y Errores

- Se aplanan los arrays `all_predictions`, `all_labels` y `errors` para facilitar la creación de un DataFrame.
- Se crea un DataFrame `df` que contiene las predicciones, las etiquetas reales y los errores correspondientes.
- Este DataFrame se guarda en `predictions_Replicate.csv`.

#### 9.2 Guardado de Pérdidas de Entrenamiento y Validación

- Se crea un DataFrame `df1` con las pérdidas de entrenamiento (`train_losses`) y validación (`val_losses`) por época.
- Este DataFrame se guarda en `Train_Val_losses_Replicate.csv`.

In [20]:
# Asegurar que los datos sean listas planas
all_predictions = np.array(all_predictions).ravel()
all_labels = np.array(all_labels).ravel()
errors = np.array(errors).ravel()

# Crear un DataFrame con los datos
df = pd.DataFrame({
    "Predictions": all_predictions,
    "Labels": all_labels,
    "Errors": errors
})

df1 = pd.DataFrame({
    "Train_losses": train_losses,
    "Val_losses": val_losses
})

# Guardar el DataFrame en un archivo CSV
df.to_csv("predictions_Replicate.csv", index=False, encoding="utf-8")

# Guardar el DataFrame en un archivo CSV
df.to_csv("Train_Val_losses_Replicate.csv", index=False, encoding="utf-8")

print("Datos guardados en predicciones.csv")

Datos guardados en predicciones.csv


#### 9.3 Guardado de Correlaciones

- Se crea un DataFrame `df2` con los coeficientes de correlación calculados para cada salida.
- Este DataFrame se guarda en `Correlations_Replicate.csv`.

In [21]:
df2 = pd.DataFrame({
    "Correlations": correlations
})

df.to_csv("Correlations_Replicate.csv", index=False, encoding="utf-8")

print("Datos guardados en Correlations_Replicate.csv")

Datos guardados en Correlations_Replicate.csv


### 10. Evaluación con Errores Normalizados (Coeficientes 1 y 2)

Esta sección introduce una función de evaluación similar a la anterior, pero con una normalización específica aplicada a los errores de los dos primeros coeficientes de Zernike.

#### 10.1 `evaluate_and_plot_test_norm`

Esta función es una variante de `evaluate_and_plot_test` con una adición clave:
- **Normalización Específica**: Los errores de los coeficientes 1 y 2 (índices 0 y 1 en un array) se normalizan dividiéndolos por 8.38. Esta normalización podría estar relacionada con un rango esperado o una escala particular de estos coeficientes en el dominio del problema.

El resto de las funcionalidades (cálculo de métricas, generación de diagramas de cajas, histogramas y gráficos de líneas de errores) son idénticas a `evaluate_and_plot_test`, pero los títulos de los gráficos y los nombres de los archivos HTML (`Boxplot_Norm_1_2.html`, `Histogram_Prediction_Errors_norm_1_2.html`, `Lineplot_Errors_Per_Coefficient_norm_1_2.html`) reflejan esta normalización.

In [22]:
# Función para evaluar el modelo y graficar resultados de forma interactiva
def evaluate_and_plot_test_norm(loader, model, criterion, dataset_name=""):
    model.eval()
    total_loss = 0.0
    all_labels = []
    all_predictions = []

    with torch.no_grad():
        for images, labels in loader:
            images, labels = images.to(device), labels.to(device)
            outputs = model(images)
            loss = criterion(outputs, labels)
            total_loss += loss.item()

            all_labels.append(labels.cpu().numpy())
            all_predictions.append(outputs.cpu().numpy())

    mse_avg_loss = total_loss / len(loader)
    rmse_avg = torch.sqrt(torch.tensor(mse_avg_loss))

    # Convertir listas en arrays para análisis
    all_labels = np.concatenate(all_labels, axis=0)
    all_predictions = np.concatenate(all_predictions, axis=0)

    # Calcular métricas adicionales
    mae = mean_absolute_error(all_labels, all_predictions)
    r2 = r2_score(all_labels, all_predictions)

    # Imprimir métricas
    print(f'[{dataset_name}] Loss (MSE): {mse_avg_loss:.4f}')
    print(f'[{dataset_name}] Loss (RMSE): {rmse_avg:.4f}')
    print(f'[{dataset_name}] MAE: {mae:.4f}')
    print(f'[{dataset_name}] R²: {r2:.4f}')

    # Calcular el error absoluto para cada coeficiente
    errors = all_predictions - all_labels

    # Normalizar errores para coeficientes 1 y 2 (Min-Max Scaling)
    errors[:, 0] = errors[:, 0]  / 8.38
    errors[:, 1] = errors[:, 1]  / 8.38


    df_errors = pd.DataFrame(errors, columns=[f'Coef {i+1}' for i in range(errors.shape[1])])
    df_melted = df_errors.melt(var_name='Coeficiente', value_name='Error')

    fig = px.box(df_melted, x='Coeficiente', y='Error', color='Coeficiente',
                 title='Diagrama de Cajas de Errores por Coeficiente Norm 1 y 2')

    # Crear histograma interactivo de errores

    fig2 = px.histogram(errors, nbins=30, labels={'value': 'Prediction Error'},
                        title=f'{dataset_name}: Histogram of Prediction Errors Norm 1 y 2', opacity=0.7)

    # Crear figura de líneas para errores por coeficiente
    fig3 = go.Figure()

    num_bins = 100  # Puedes ajustar este número según el detalle deseado

    # Crear una línea para cada coeficiente
    for i in range(errors.shape[1]):
        hist, bin_edges = np.histogram(errors[:, i], bins=num_bins)
        bin_centers = 0.5 * (bin_edges[:-1] + bin_edges[1:])

        fig3.add_trace(go.Scatter(
            x=bin_centers,
            y=hist,
            mode='lines',
            name=f'Coef {i+1}'
        ))

    fig3.update_layout(
        title=f'{dataset_name}: Frecuencia del Error de Predicción por Coeficiente Norm 1 y 2',
        xaxis_title='Error de Predicción',
        yaxis_title='Frecuencia',
        template='plotly_white'
    )


    fig.show()
    fig2.show()
    fig3.show()

    fig.write_html("Boxplot_Norm_1_2.html")
    fig2.write_html("Histogram_Prediction_Errors_norm_1_2.html")
    fig3.write_html("Lineplot_Errors_Per_Coefficient_norm_1_2.html")

    return rmse_avg, mse_avg_loss, mae, r2, all_predictions, all_labels, errors

#### 10.2 Evaluación del Modelo con Normalización de Errores

Se llama a la función `evaluate_and_plot_test_norm` para evaluar el modelo en el conjunto de prueba, aplicando la normalización específica a los errores de los coeficientes 1 y 2. Esto permite un análisis más detallado del rendimiento del modelo en función de estas métricas normalizadas.

In [23]:
# Evaluar en los conjuntos de Test y Validation
test_loss,test_loss_rmse, test_mae, test_r2, all_predictions, all_labels, errors = evaluate_and_plot_test_norm(test_loader, model, criterion, "Test Set")

[Test Set] Loss (MSE): 1.0216
[Test Set] Loss (RMSE): 1.0107
[Test Set] MAE: 0.6408
[Test Set] R²: 0.0582
